<a href="https://colab.research.google.com/github/justingis/address_geocoding/blob/main/parcel_analyzer_coloab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Parcel Analyzer
This notebook takes input land parcels in shapefile format and determines which ones are landlocked. Landlocked parcels are determined by running a spatial intersect analysis with buffered parcels and OpenStreetMap roads. If no roads intersect a buffered parcel, that parcel is considered landlocked.

1. Copy extracted shapefiles from LandVision to shp folder on Google Drive: https://drive.google.com/drive/folders/1ZLxYtQ0eCsP4qtz8jvXx8LkNtC8nAin2?usp=drive_link
 Make sure to include the 4 required files that make up a single shapefile (.shp, .dbf, .prj, .shx)

2. Assign the shapefile name and parcel buffer distance in feet to the variables below:

In [53]:
shapefile_name = 'ParcelDetail_1.shp'
buffer_distance_ft = 100.0

3. Click Runtime --> Run all from the main menu at the top of the page. Scroll to the bottom of the notebook to view the output map. Upon completion, a message at the end of the notebook will notify the user the analysis is complete. The output CSV file will be created here: https://drive.google.com/drive/folders/10VE3XLHQN61eRRcECRBiuCK877cOrso6?usp=drive_link

In [55]:
# Import Python libraries
import warnings
import pandas as pd
import numpy as np
import geopandas as gpd
import osmnx as ox
import os
import leafmap.foliumap as leafmap
from tqdm.notebook import tqdm
from shapely.geometry import box
from shapely.geometry import LineString, MultiLineString
from google.colab import drive
drive.mount('/content/drive')
warnings.filterwarnings('ignore')

# Set parcels shapefile name and folder path
shapefile_folder = '/content/drive/MyDrive/shp'
csv_folder = '/content/drive/MyDrive/csv'
parcels_path = os.path.join(shapefile_folder, shapefile_name)
csv_path = os.path.join(csv_folder, shapefile_name.replace('.shp', '.csv'))

# Set parcel buffer distance in feet
buffer_distance_m = buffer_distance_ft * 0.3048 # convert feet to meters

parcels_gdf = gpd.read_file(parcels_path) # create geodataframe from parcels shapefile

# View the % complete for each column in the parcels dataframe
completeness = (1 - parcels_gdf.isna().mean()) * 100
data_types = parcels_gdf.dtypes
column_info = pd.DataFrame({
    'Completeness (%)': completeness,
    'Data Type': data_types
})

# Run intersect analysis with OpenStreetMap roads. Warning message may be ignored
# Number of landlocked parcels will display when finished
parcels_gdf = parcels_gdf.to_crs('EPSG:5070')

buffered_parcels_gdf = parcels_gdf.copy()
buffered_parcels_gdf['geometry'] = buffered_parcels_gdf.geometry.buffer(buffer_distance_m)

buffered_parcels_gdf_wgs84 = buffered_parcels_gdf.to_crs('EPSG:4326')
minx, miny, maxx, maxy = buffered_parcels_gdf_wgs84.total_bounds
bbox = (miny, minx, maxy, maxx)

tags = {'highway': True}
roads = ox.geometries_from_bbox(north=bbox[2], south=bbox[0], east=bbox[3], west=bbox[1], tags=tags)

roads_gdf = gpd.GeoDataFrame(roads, geometry='geometry')
roads_gdf = roads_gdf[roads_gdf.geometry.apply(lambda geom: isinstance(geom, (LineString, MultiLineString)))] # remove points, keep only lines

roads_gdf = roads_gdf.to_crs('EPSG:5070')

non_intersecting_parcels_gdf = buffered_parcels_gdf[~buffered_parcels_gdf.intersects(roads_gdf.unary_union)]

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [56]:
# View parcels geodataframe record counts and columns
parcels_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 1432 entries, 0 to 1431
Data columns (total 23 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   APN       1432 non-null   object  
 1   OWNER_2   1168 non-null   object  
 2   OWNER_AE  709 non-null    object  
 3   OWNER_9B  1168 non-null   object  
 4   COUNTY    1168 non-null   object  
 5   SITE_S15  1168 non-null   object  
 6   MAIL_A9D  1154 non-null   object  
 7   MAIL_CBB  1154 non-null   object  
 8   MAIL_S3   1154 non-null   object  
 9   MAIL_ZIP  1147 non-null   object  
 10  ACREAGE   1432 non-null   float64 
 11  YR_BLT    529 non-null    float64 
 12  TAX_YE99  0 non-null      object  
 13  TAX_ID    1168 non-null   object  
 14  PARCELF5  1432 non-null   object  
 15  ALTERNDE  1168 non-null   object  
 16  OWNER_55  0 non-null      object  
 17  LAST_L99  770 non-null    float64 
 18  VAL_TRA7  4 non-null      float64 
 19  SITE_AAF  916 non-null    object  
 20  

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [57]:
# View the % complete for each column in the parcels dataframe
column_info

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Completeness (%) Data Type
APN             100.000000    object
OWNER_2          81.564246    object
OWNER_AE         49.511173    object
OWNER_9B         81.564246    object
COUNTY           81.564246    object
SITE_S15         81.564246    object
MAIL_A9D         80.586592    object
MAIL_CBB         80.586592    object
MAIL_S3          80.586592    object
MAIL_ZIP         80.097765    object
ACREAGE         100.000000   float64
YR_BLT           36.941341   float64
TAX_YE99          0.000000    object
TAX_ID           81.564246    object
PARCELF5        100.000000    object
ALTERNDE         81.564246    object
OWNER_55          0.000000    object
LAST_L99         53.770950   float64
VAL_TRA7          0.279330   float64
SITE_AAF         63.966480    object
SITE_CCD         81.564246    object
SITE_ZIP         75.069832    object
geometry        100.000000  geometry

In [58]:
# Display landlocked parcels on map. Yellow parcels are landlocked

non_intersect_index_vals = non_intersecting_parcels_gdf.index.tolist()
non_intersect_display = parcels_gdf.loc[non_intersect_index_vals]

non_intersect_display = non_intersect_display.to_crs('4326')
parcels_gdf_display = parcels_gdf.to_crs('4326')
parcels_gdf_display = parcels_gdf_display.drop(non_intersect_index_vals)
roads_display = roads_gdf.to_crs('4326')
m = leafmap.Map()
m.add_basemap("HYBRID")

m.add_gdf(parcels_gdf_display)
parcels_gdf_display.explore(m=m, color='gray', tooltip=False, popup=False, style_kwds={'fillOpacity': 0})

non_intersect_display.explore(m=m,color = 'yellow', style_kwds={'fillOpacity': 0})


m.add_gdf(roads_display)
roads_display.explore(m=m, color='purple', tooltip=False, popup=False)

m.zoom_to_gdf(non_intersect_display)
m

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [59]:
# Export output CSV file
# CSV file gets written to same location as input shapefile with same name
#print(len(non_intersect_display), len(parcels_gdf_display))
non_intersect_display['Land_Locked'] = 'Yes'
non_intersect_display['Buffer_Distance'] = str(buffer_distance_ft) +' ft'

csv_export_df = pd.concat([non_intersect_display, parcels_gdf_display], axis=0)
csv_export_df = csv_export_df.reset_index(drop=True)
csv_export_df = csv_export_df.drop(columns='geometry')
csv_export_df.to_csv(csv_path, index=False)

print(f'{len(non_intersecting_parcels_gdf)} landlocked parcels')
print(f'Analysis complete. See {csv_path}')

22 landlocked parcels
Analysis complete. See /content/drive/MyDrive/csv/ParcelDetail_1.csv


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
